<a href="https://colab.research.google.com/github/AlexLynd/ESP8266-Wardriving/blob/master/JN-Scripts/Missoula-Warflight-08-21-2021.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# **Missoula WarFlight 08/21/2021**

This notebook explores wardriving data captured in Missoula during our first aerial reconnaissance test, using an ESP8266 + hardware peripherals strapped to a Mavic Pro quadcopter.  The goal was to capture the location of 2 target networks my friend Kody and I set up, `Target3` and `Bingus Mobile`.

# **Import and Clean WarFlight DataSet**

We start by importing the CSV file generated from the ESP8266 wardriving rig, which is formatted to the [WiGLE CSV](https://api.wigle.net/csvFormat.html) convention.  Since an excess of duplicate networks were detected when the drone was sitting idle during takeoff / landing, we filter those networks out by adding a time filter.  We detected `341 unique networks` in about `3 minutes` of flight time.

In [9]:
# import dataset

import pandas as pd
wd = pd.read_csv ('./Missoula-Warflight-08-21-2021.csv', delimiter = ',')  # read warflight csv file into Pandas dataframe

print("Total WiFi AP entries: " + str(len(wd)))
wd.sample(10)  # 10 random networks

Total WiFi AP entries: 5293


MAC                           SSID  ... AccuracyMeters  Type
4353  2A:E8:29:14:23:9B  Missoula Paddleheads  - Guest  ...            160  WIFI
3712  70:F2:20:E1:21:93                CenturyLink4634  ...            160  WIFI
2320  A4:13:4E:42:48:00                 Luxul_XWO-BAP1  ...            159  WIFI
1167  C8:B4:22:C1:43:51            MySpectrumWiFi53-2G  ...            242  WIFI
1338  0C:9D:92:2B:9B:88                            TCI  ...            244  WIFI
1174  FE:EC:DA:97:BE:69               Poverello Center  ...            242  WIFI
413   64:A5:C3:70:82:64                    Black Death  ...            236  WIFI
1102  2A:E8:29:14:23:3A  Missoula Paddleheads  - Guest  ...            242  WIFI
139   2A:E8:29:5A:1B:8C  Missoula Paddleheads  - Guest  ...            291  WIFI
1571  94:A6:7E:65:51:C4                    BurritoShop  ...            185  WIFI

[10 rows x 11 columns]

In [10]:
# clean dataset by dropping excessive data entries

wd.drop(wd.index[wd["FirstSeen"] <= "2021-8-21 18:43:25"],0, inplace=True) # before takeoff
wd.drop(wd.index[wd["FirstSeen"] >= "2021-8-21 18:46:58"],0, inplace=True) # after landing

print("Total WiFi AP entries: " + str(len(wd)))
print("Unique network entries: " + str(len(wd.SSID.unique())))

Total WiFi AP entries: 1938
Unique network entries: 341


# **Map All Data Entries + WarFlying Route**

A generic cluster plot showing all 1938 detected network entries, juxtaposed on the warflight path w/ marked takeoff and landing times.  

In [11]:
# plot all network entries as a cluster map w/ warflight route

import folium
from folium import FeatureGroup, LayerControl, Map, Marker
from folium.plugins import MarkerCluster

MarkerCluster()

# autofit map boundaries from dataset
wd_net_map = folium.Map(wd[['Latitude', 'Longitude']].mean().values.tolist())
wd_net_map.fit_bounds([wd[['Latitude', 'Longitude']].min().values.tolist(), wd[['Latitude', 'Longitude']].max().values.tolist()])
network_cluster = MarkerCluster().add_to(wd_net_map)

# convert dataframe to array
networks = wd.values

# warflight route
folium.PolyLine(wd[['Latitude', 'Longitude']].values.tolist(),line_opacity = 0.5, weight = 4).add_to(wd_net_map)

# cluster map of all network entries
for network in networks: folium.Marker([network[6],network[7]], popup=network[1], icon=folium.Icon(color='darkblue', icon_color='white', icon='wifi', angle=0, prefix='fa')).add_to(network_cluster)

# first and last data entry
folium.Marker([networks[0][6], networks[0][7]], popup=networks[0][3], icon=folium.Icon(color='green', icon_color='white', icon='plane', angle=0, prefix='fa')).add_to(wd_net_map)
folium.Marker([networks[len(networks)-1][6],networks[len(networks)-1][7]], popup= networks[len(networks)-1][3], icon=folium.Icon(color='red', icon_color='white', icon='plane', angle=0, prefix='fa')).add_to(wd_net_map)

display(wd_net_map)

# **Known Devices + Network HeatMap**

This heatmap depicts the generic concentration of networks we spotted during the flight, and also points where the known networks were spotted.  `Bingus Mobile` was spotted twice since I had to run to my designated spot while Kody had already started warflying, thus registering multiple location entries.  `Target3` which was manned by our friend Cristian, was detected successfully.

In [12]:
# network concentration heat map + known device location

known_devices = ["Target3", "Bingus Mobile"]

import folium, numpy
from folium import Map, Marker, plugins

# autofit map boundaries from dataset
wd_heat_map = folium.Map(wd[['Latitude', 'Longitude']].mean().values.tolist())
wd_heat_map.fit_bounds([wd[['Latitude', 'Longitude']].min().values.tolist(), wd[['Latitude', 'Longitude']].max().values.tolist()])

for device in wd.loc[wd["SSID"].isin(known_devices)].values:
  folium.Marker( location=[device[6], device[7]], popup=device[1], icon=folium.Icon(color="darkblue",icon='wifi',prefix='fa')).add_to(wd_heat_map)

wd_heat_map.add_child(plugins.HeatMap(wd[['Latitude', 'Longitude']].to_numpy(), radius=30))
display(wd_heat_map)

# **WiFi Network Encryption Filter**

This feature map lets you view and toggle WiFi networks by encryption type.  There were a surprising amount of open / unsecured networks! 

In [13]:
import folium
from folium import FeatureGroup, LayerControl, Map, Marker

wd_encryption_map = folium.Map(wd[['Latitude', 'Longitude']].mean().values.tolist())
wd_encryption_map.fit_bounds([wd[['Latitude', 'Longitude']].min().values.tolist(), wd[['Latitude', 'Longitude']].max().values.tolist()])

# map feature groups for different encryption types
wep_feature_group = folium.FeatureGroup("WEP")
wpa_feature_group = folium.FeatureGroup("WPA")
wpa2_feature_group = folium.FeatureGroup("WPA2")
opn_feature_group = folium.FeatureGroup("Open")
none_feature_group = folium.FeatureGroup("None")

# convert dataframe to array
networks = wd.values

# add network coordinates
for network in networks:
  if   (network[2] == "[WPA-PSK-CCMP+TKIP][ESS]"):
    folium.Marker(location=[network[6],network[7]],  popup=network[1], icon=folium.Icon(color="blue",icon='user-secret',prefix='fa')).add_to(wpa_feature_group)

  elif (network[2] == "[WPA2-PSK-CCMP+TKIP][ESS]"):
    folium.Marker(location=[network[6],network[7]],  popup=network[1], icon=folium.Icon(color="green",icon='user-secret',prefix='fa')).add_to(wpa2_feature_group)

  elif (network[2] == "[WEP][ESS]"):
    folium.Marker(location=[network[6],network[7]],  popup=network[1], icon=folium.Icon(color="red",icon='user-secret',prefix='fa')).add_to(wep_feature_group)

  elif (network[2] == "[ESS]"):
    folium.Marker(location=[network[6],network[7]],  popup=network[1], icon=folium.Icon(color="orange",icon='user-secret',prefix='fa')).add_to(opn_feature_group)

  elif (network[2] == "[WPA-PSK-CCMP+TKIP][WPA2-PSK-CCMP+TKIP][ESS]"):
    folium.Marker(location=[network[6],network[7]],  popup=network[1], icon=folium.Icon(color="purple",icon='user-secret',prefix='fa')).add_to(none_feature_group)

# add feature groups to map 
wep_feature_group.add_to(wd_encryption_map)
wpa_feature_group.add_to(wd_encryption_map)
wpa2_feature_group.add_to(wd_encryption_map)
opn_feature_group.add_to(wd_encryption_map)
none_feature_group.add_to(wd_encryption_map)

folium.LayerControl().add_to(wd_encryption_map)

display(wd_encryption_map)